In [1]:
%env SM_FRAMEWORK=tf.keras
from segmentation_models.losses import binary_focal_dice_loss
from segmentation_models.metrics import IOUScore, FScore
import segmentation_models as sm
import tensorflow as tf
tf.keras.backend.set_image_data_format('channels_last')

env: SM_FRAMEWORK=tf.keras
Segmentation Models: using `tf.keras` framework.


In [4]:
!pip install tensorflow==2.14.0

   ---------------------------------------- 0.0/284.2 MB ? eta -:--:--
   ---------------------------------------- 1.0/284.2 MB 33.4 MB/s eta 0:00:09
   ---------------------------------------- 1.0/284.2 MB 33.4 MB/s eta 0:00:09
   ---------------------------------------- 2.0/284.2 MB 15.6 MB/s eta 0:00:19
   ---------------------------------------- 2.1/284.2 MB 16.6 MB/s eta 0:00:17
   ---------------------------------------- 2.1/284.2 MB 16.6 MB/s eta 0:00:17
   ---------------------------------------- 3.1/284.2 MB 13.4 MB/s eta 0:00:21
   ---------------------------------------- 3.1/284.2 MB 13.4 MB/s eta 0:00:21
    --------------------------------------- 4.2/284.2 MB 12.7 MB/s eta 0:00:22
    --------------------------------------- 4.2/284.2 MB 12.7 MB/s eta 0:00:22
    --------------------------------------- 4.7/284.2 MB 11.2 MB/s eta 0:00:25
    --------------------------------------- 5.2/284.2 MB 11.9 MB/s eta 0:00:24
    --------------------------------------- 5.2/284.2 MB 11.

In [6]:
from tensorflow.keras.utils import custom_object_scope

In [8]:
model = tf.keras.models.load_model('my_model.h5', custom_objects={'binary_focal_loss_plus_dice_loss': sm.losses.binary_focal_dice_loss,
                                                                   'iou_score': sm.metrics.IOUScore,
                                                                   'f1-score': sm.metrics.FScore})

In [9]:
model.weights

[<tf.Variable 'bn_data/beta:0' shape=(3,) dtype=float32, numpy=array([ 0.04700802, -0.11150173,  0.06720523], dtype=float32)>,
 <tf.Variable 'bn_data/moving_mean:0' shape=(3,) dtype=float32, numpy=array([22.151236, 21.236992, 23.189302], dtype=float32)>,
 <tf.Variable 'bn_data/moving_variance:0' shape=(3,) dtype=float32, numpy=array([1071.462 ,  990.2634, 1164.8427], dtype=float32)>,
 <tf.Variable 'conv0/kernel:0' shape=(7, 7, 3, 64) dtype=float32, numpy=
 array([[[[ 1.73711777e-03,  1.53363012e-02,  3.50671299e-02, ...,
           -1.07975267e-02,  4.23867814e-02,  3.84291224e-02],
          [ 1.71777084e-02,  1.06854476e-02,  4.15595807e-02, ...,
            2.72011943e-02, -4.18588631e-02,  1.34172589e-02],
          [ 1.34363919e-02, -4.04350460e-03, -6.20147586e-03, ...,
            1.62595995e-02,  1.88003927e-02, -8.64036381e-04]],
 
         [[ 3.02905627e-02,  2.19163410e-02,  2.17549093e-02, ...,
           -1.43577736e-02, -2.08088756e-03,  1.77090727e-02],
          [-4.076

In [10]:
!pip install tensorflow pillow python-docx reportlab opencv-python

   ---------------------------------------- 0.0/244.3 kB ? eta -:--:--
   ----- ---------------------------------- 30.7/244.3 kB 1.4 MB/s eta 0:00:01
   ---------------------------------------- 244.3/244.3 kB 3.8 MB/s eta 0:00:00
   ---------------------------------------- 0.0/1.9 MB ? eta -:--:--
   ------------- -------------------------- 0.7/1.9 MB 14.2 MB/s eta 0:00:01
   ---------------------------------------  1.9/1.9 MB 20.4 MB/s eta 0:00:01
   ---------------------------------------- 1.9/1.9 MB 20.8 MB/s eta 0:00:00


In [93]:
import tensorflow as tf
from tensorflow.keras.models import load_model
from PIL import Image, ImageDraw
import numpy as np
import cv2
from docx import Document
from docx.shared import Inches
from reportlab.pdfgen import canvas
from reportlab.lib.pagesizes import A4
import segmentation_models as sm
from PIL import ImageDraw

In [14]:
BACKBONE = 'resnext50'
preprocess_input = sm.get_preprocessing(BACKBONE)

In [71]:
def preprocess_image(image_path):
    """ Preprocess the image for prediction based on the training steps in the notebook. """
    img = cv2.imread(image_path)
    img = cv2.resize(img, (256, 256))  # Resize image to match model's expected input size
    img = preprocess_input(img)  # Use segmentation_models preprocessing
    img_array = np.expand_dims(img, axis=0)  # Add batch dimension
    return Image.fromarray(cv2.cvtColor(img, cv2.COLOR_BGR2RGB)), img_array

In [72]:
def predict_tumor(image_array, threshold=0.5):
    """ Predict whether there is a tumor. """
    pr_mask = model.predict(image_array)
    
    # Assuming pr_mask is a probability map or segmentation mask
    if isinstance(pr_mask, list):
        pr_mask = pr_mask[-1]  # Take the last prediction if multiple outputs

    # For binary segmentation with sigmoid activation, threshold the prediction
    pr_mask_binary = (pr_mask > threshold).astype(np.uint8)
    
    return pr_mask_binary

In [126]:
def highlight_tumor(original_img, image_array):
    """ Highlight the tumor region on the image with a bounding box. """
    segmentation_map = predict_tumor(image_array)
    
    # If segmentation map has more than 2 dimensions, we need to handle this.
    if segmentation_map.ndim > 2:
        segmentation_map = np.squeeze(segmentation_map, axis=0)  # Remove the channel dimension if it exists
    
    # Resize the segmentation map to match the original image dimensions
    segmentation_map_resized = cv2.resize(segmentation_map, (original_img.size[0], original_img.size[1]), interpolation=cv2.INTER_NEAREST)

    # Ensure the segmentation map is a 2D array
    if segmentation_map_resized.ndim != 2:
        raise ValueError("The segmentation map should be a 2D array.")

    # Find the bounding box coordinates of the tumor region
    y_indices, x_indices = np.where(segmentation_map_resized == 1)
    if len(x_indices) == 0 or len(y_indices) == 0:
        return original_img  # No tumor region detected, return the original image

    x_min, x_max = x_indices.min(), x_indices.max()
    y_min, y_max = y_indices.min(), y_indices.max()

    # Draw a bounding box around the tumor region
    overlay = original_img.copy()
    draw = ImageDraw.Draw(overlay)
    draw.rectangle([x_min, y_min, x_max, y_max], outline="red", width=3)  # Draw bounding box with red color

    return overlay

In [84]:
def create_report(image_path, has_tumor, highlighted_image=None, report_path='report.docx'):
    """ Create a report in a Word document. """
    doc = Document()
    doc.add_heading('Tumor Detection Report', 0)

    doc.add_paragraph('The result of the tumor detection is as follows:')
    if has_tumor:
        doc.add_paragraph('Tumor detected in the image.')
        highlighted_image.save('highlighted_image.png')
        doc.add_picture('highlighted_image.png', width=Inches(5.0))
    else:
        doc.add_paragraph('No tumor detected in the image.')
        img = Image.open(image_path)
        img.save('test_image.png')
        doc.add_picture('test_image.png', width=Inches(5.0))

    doc.save(report_path)

In [85]:
def create_pdf_report(image_path, has_tumor, highlighted_image=None, report_path='report.pdf'):
    """ Create a report in a PDF document. """
    c = canvas.Canvas(report_path, pagesize=A4)
    width, height = A4

    c.setFont("Helvetica-Bold", 20)
    c.drawString(100, height - 100, "Tumor Detection Report")

    c.setFont("Helvetica", 12)
    if has_tumor:
        c.drawString(100, height - 140, "Tumor detected in the image.")
        highlighted_image.save('highlighted_image.png')
        c.drawImage('highlighted_image.png', 100, height - 600, width=400, height=400)
    else:
        c.drawString(100, height - 140, "No tumor detected in the image.")
        img = Image.open(image_path)
        img.save('test_image.png')
        c.drawImage('test_image.png', 100, height - 600, width=400, height=400)

    c.save()

In [86]:
def process_and_generate_reports(image_path, docx_report_path='tumor_report.docx', pdf_report_path='tumor_report.pdf'):
    """ Process the image, predict tumor, and generate both Word and PDF reports. """
    original_img, image_array = preprocess_image(image_path)
    has_tumor = predict_tumor(image_array)

    if has_tumor.any():  # Check if any pixels are classified as tumor (assuming `has_tumor` is a binary mask)
        highlighted_img = highlight_tumor(original_img, image_array)
    else:
        highlighted_img = None

    # Generate report in Word
    create_report(image_path, has_tumor.any(), highlighted_img, report_path=docx_report_path)

    # Generate report in PDF
    create_pdf_report(image_path, has_tumor.any(), highlighted_img, report_path=pdf_report_path)

In [87]:
pos_img = 'C:/Users/KEVIN/Downloads/archive (1)/kaggle_3m\\TCGA_CS_5393_19990606/TCGA_CS_5393_19990606_6.tif'

In [45]:
neg_img = 'C:/Users/KEVIN/Downloads/archive (1)/kaggle_3m\\TCGA_CS_4941_19960909/TCGA_CS_4941_19960909_1.tif'

In [125]:
process_and_generate_reports(pos_img, docx_report_path='pos_tumor_report.docx', pdf_report_path='pos_tumor_report.pdf')

1/1 [==============================] - 0s 254ms/step


In [81]:
process_and_generate_reports(neg_img, docx_report_path='neg_tumor_report.docx', pdf_report_path='neg_tumor_report.pdf')

1/1 [==============================] - 0s 263ms/step


In [2]:
print(sm.__version__)

1.0.1
